In [1]:
from statsmodels.stats.power import tt_ind_solve_power, zt_ind_solve_power
from statsmodels.stats.proportion import proportion_effectsize
from statsmodels.stats.meta_analysis import effectsize_smd
from typing import Union
import plotly.graph_objects as go
from scipy import stats
from math import asin
import numpy as np

- effect_size - ошибка 1,2 рода(нормированная разница между группами)
- conv_1 - кол-во конвертированных пользователей в группе
- nobs_1 - кол-во всех пользователей (кол-во наблюдений в контроле  = None - для одной из групп  *2 - чтобы получить общую выборку)
- alpha - значение ошибки 1 рода
- power = (1 - beta(ошибка 2 рода))
- ratio - отношение (между 1 выборкой и 2) количества наблюдений в тесте к контролю
-  prob_1, prob_2 - вероятность события
- alternative = 'two-sided' - двусторонняя проверка гипотез

In [2]:
#Расчёт effect_size для пропорций
def calc_propotion_effect_size(conv_1: int, nobs_1: int, conv_2: int, nobs_2: int):
    prob_1, prob_2 = conv_1 / nobs_1, conv_2 / nobs_2
    
    es_formula = 2  * asin(np.sqrt(prob_1)) - 2 * asin(np.sqrt(prob_2))
    es_import = proportion_effectsize(prob_1, prob_2)
    
    return es_formula, es_import

#Расчёт effect_size для непрерывных метрик
def calc_continuous_effect_size(mean_1: Union[float, int],
                                std_1: Union[float, int],
                                mean_2: Union[float, int],
                                std_2: Union[float, int],
                                nobs_1: int = 10_000,
                                nobs_2: int = 10_000):
    
    es_formula = (mean_1 - mean_2) / ((std_1**2 + std_2**2) / 2) ** 0.5
    es_import = effectsize_smd(mean_1, std_1, nobs_1, mean_2, std_2, nobs_2)[0]
    
    return es_formula, es_import 

In [3]:
#Расчёт минимально необходимой выборки * 2(для теста и контроля) для пропорций
def calc_sample_size_proportion(effect_size: float,
                                alpha: float = .05,
                                beta: float = .2,
                                ratio: Union[float, int] = 1):
    
    n = zt_ind_solve_power(effect_size=effect_size,
                           alpha=alpha,
                           power=(1 - beta),
                           ratio=ratio,
                  )
    return int(n * 2)
#Расчёт минимально необходимой выборки * 2(для теста и контроля) для непрерывной метрики
def calc_sample_size_continuous(effect_size: float,
                                alpha: float = .05,
                                beta: float = .2,
                                ratio: Union[float, int] = 1):
    
    n = tt_ind_solve_power(effect_size=effect_size,
                           alpha=alpha,
                           power=(1 - beta),
                           ratio=ratio,
                  )
    return int(n * 2)

### Задание 1

Мы хотим провести АБ-тест баннеров.
- Нынешняя конверсия в клик на баннер (CTR) равна 1.5%. 
- Мы предполагаем, что с новыми баннерами CTR вырастет до 1.7%. 
- Определите, сколько юзеров нам нужно отправить на каждую версию с уровнем доверия 95%

In [4]:
mu_control, mu_test = 2167, 2180
std_control, std_test = 69, 69# * 1.15

calc_continuous_effect_size(mean_1=mu_control, std_1=std_control, mean_2=mu_test, std_2=std_test) #-0.18840579710144928

(-0.18840579710144928, -0.18839873108913158)

In [5]:
effect_size = calc_continuous_effect_size(mean_1=mu_control, std_1=std_control, mean_2=mu_test, std_2=std_test)[1]
calc_sample_size_continuous(effect_size=effect_size, alpha=.05, beta=.2)

886

In [6]:
conv_1, conv_2 = 15, 17
nobs_1, nobs_2 = 1000, 1000
prob_1, prob_2 = conv_1 / nobs_1, conv_2 / nobs_2 #0.015, 0.017
print(prob_1, prob_2)
calc_propotion_effect_size(conv_1=conv_1, nobs_1=nobs_1, conv_2=conv_2, nobs_2=nobs_2)

0.015 0.017


(-0.015947131645016377, -0.015947131645016377)

количество необходимых эксперементов для 2 выборок (контроля и теста)

In [7]:
effect_size = calc_propotion_effect_size(conv_1=conv_1, nobs_1=nobs_1, conv_2=conv_2, nobs_2=nobs_2)[0]
calc_sample_size_proportion(effect_size=effect_size, alpha=.05, beta=.2)

123452

###### тест 1

In [8]:
effect_size = calc_propotion_effect_size(conv_1=conv_1, nobs_1=nobs_1, conv_2=conv_2, nobs_2=nobs_2)[0]
alpha =.05
beta =.2
nobs1 = None
ratio = 1
zt_ind_solve_power(effect_size=effect_size,
                           alpha=alpha,
                           power=(1 - beta),
                           nobs1 = None,
                           ratio=ratio,)

61726.470908232826

###### тест 2

In [9]:
effect_size = calc_propotion_effect_size(conv_1=conv_1, nobs_1=nobs_1, conv_2=conv_2, nobs_2=nobs_2)[0]
alpha = None
beta =.2
nobs1 = 61726
ratio = 1
zt_ind_solve_power(effect_size=effect_size,
                           alpha=alpha,
                           power=(1 - beta),
                           nobs1=nobs1,
                           ratio=ratio,)

0.049999906355427365

###### тест 3

In [10]:
effect_size = calc_propotion_effect_size(conv_1=conv_1, nobs_1=nobs_1, conv_2=conv_2, nobs_2=nobs_2)[0]
alpha = .05
power = None#(1- beta)
nobs1 = 61726
ratio = 1
zt_ind_solve_power(effect_size=effect_size,
                           alpha=alpha,
                           power=power,
                           nobs1=nobs1,
                           ratio=ratio,)

0.7999970081917244

###### тест 4

In [11]:
effect_size = calc_propotion_effect_size(conv_1=conv_1, nobs_1=nobs_1, conv_2=conv_2, nobs_2=nobs_2)[0]
alpha = .05
power = (1- 0.2)
nobs1 = 61726
ratio = None
zt_ind_solve_power(effect_size=effect_size,
                           alpha=alpha,
                           power=power,
                           nobs1=nobs1,
                           ratio=ratio,)
# n1 = ratio *n2

1.000015973591064

###### тест 5

In [12]:
effect_size = None#calc_propotion_effect_size(conv_1=conv_1, nobs_1=nobs_1, conv_2=conv_2, nobs_2=nobs_2)[0]
alpha = .05
power = (1- 0.2)
nobs1 = 61726
ratio = 1
zt_ind_solve_power(effect_size=effect_size,
                           alpha=alpha,
                           power=power,
                           nobs1=nobs1,
                           ratio=ratio,)

0.015949309973587938

### Задание 2

Мы хотим провести АБ-тест формы подтверждения заказа. 
- Нынешняя конверсия в заказ равна 3%. Мы предполагаем, что конверсия вырастет на 0,1%. 
- Определите, сколько юзеров нам нужно отправить на каждую версию с уровнем доверия 99% и уровнем мощности 90%

In [13]:
conv_1, conv_2 = 3, 3.1
nobs_1, nobs_2 = 100, 100
prob_1, prob_2 = conv_1 / nobs_1, conv_2 / nobs_2 #0.015, 0.017
print(prob_1, prob_2)
calc_propotion_effect_size(conv_1=conv_1, nobs_1=nobs_1, conv_2=conv_2, nobs_2=nobs_2)

0.03 0.031


(-0.005815545699511593, -0.005815545699511593)

In [14]:
effect_size = calc_propotion_effect_size(conv_1=conv_1, nobs_1=nobs_1, conv_2=conv_2, nobs_2=nobs_2)[0]
calc_sample_size_proportion(effect_size=effect_size, alpha=.01, beta=.1)

1759803

### Задание 3 (непрерывная метрика)

Дизайнер предложил добавить рекомендательную систему на этапе формирования корзины. 
- Нынешний средний чек равен 2167 рублей, а стандартная ошибка (SD) равна 69. 
- Мы предполагаем, что в новой версии средний чек вырастет на 2180. 
- Определите, сколько юзеров нам нужно отправить на каждую версию с уровнем доверия 95%

###### тест 1
стандартные отклонения равны

In [15]:
mu_control, mu_test = 2167, 2180
std_control, std_test = 69, 69 # * 1.15

calc_continuous_effect_size(mean_1=mu_control, std_1=std_control, mean_2=mu_test, std_2=std_test)

(-0.18840579710144928, -0.18839873108913158)

In [16]:
effect_size = calc_continuous_effect_size(mean_1=mu_control, std_1=std_control, mean_2=mu_test, std_2=std_test)[1]
calc_sample_size_continuous(effect_size=effect_size, alpha=.05, beta=.2)

886

###### тест 2   
увеличиваем стандартное отклонение тестовой группы на 15 % для неравенства дисперсий (для получения более достоверных данных)

In [17]:
mu_control, mu_test = 2167, 2180
std_control, std_test = 69, 69 * 1.15 # увеличение

calc_continuous_effect_size(mean_1=mu_control, std_1=std_control, mean_2=mu_test, std_2=std_test)

(-0.17483621585265752, -0.17482965875688977)

In [18]:
effect_size = calc_continuous_effect_size(mean_1=mu_control, std_1=std_control, mean_2=mu_test, std_2=std_test)[1]
calc_sample_size_continuous(effect_size=effect_size, alpha=.05, beta=.2)

1029

### Задание 4

Вы решили сравниваем метрику деньги на юзера в двух группах. 
- Размер выборки - 1000 элементов в каждой группе. 
- Для проверки нормальности распределения на выборке в 1000 наблюдений применили , критерий Шапиро-Уилка и получили p-value, равный 0.00002, alpha = 5% то какой бы вывод мы могли сделать в данном случае? 
- В этом случае какой статистический критерий для проверки первоначальной гипотезы тут лучше всего подойдёт и почему ?

###### тест 1

In [19]:
size = 4999
normal_distr = stats.norm.rvs(size=size)
uniform_distr = stats.uniform.rvs(size=size)
expon_distr = stats.expon.rvs(size=size)

In [20]:
fig = go.Figure()
fig.add_trace(go.Histogram(x=normal_distr, name='normal_distr',))
fig.add_trace(go.Histogram(x=uniform_distr, name='uniform_distr'))
fig.add_trace(go.Histogram(x=expon_distr, name='expon_distr'))

# Overlay both histograms
fig.update_layout(barmode='overlay')
# Reduce opacity to see both histograms
fig.update_traces(opacity=0.5)
fig.show()

In [21]:
distr_name = list(
    zip(
        (normal_distr, uniform_distr, expon_distr),
        ('normal_distr', 'uniform_distr', 'expon_distr')
    )
)

###### Tecт Шапиро-Уилки

In [22]:
for distr, name in distr_name:
    print(stats.shapiro(distr), name)

ShapiroResult(statistic=0.9996620416641235, pvalue=0.5915319919586182) normal_distr
ShapiroResult(statistic=0.9537554979324341, pvalue=4.088309120988803e-37) uniform_distr
ShapiroResult(statistic=0.8181256055831909, pvalue=0.0) expon_distr


###### Тест Колмогорова-Смирнова  'norm' нормальное

In [23]:
for distr, name in distr_name:
    print(stats.kstest(distr, 'norm'), name)

KstestResult(statistic=0.01079002405977314, pvalue=0.6015867745273833) normal_distr
KstestResult(statistic=0.5000298339761625, pvalue=0.0) uniform_distr
KstestResult(statistic=0.5000994993294112, pvalue=0.0) expon_distr


###### Тест Колмогорова-Смирнова  'uniform' равномерное

In [24]:
for distr, name in distr_name:
    print(stats.kstest(distr, 'uniform'), name)

KstestResult(statistic=0.5078212422556081, pvalue=0.0) normal_distr
KstestResult(statistic=0.012242035100720916, pvalue=0.43853562526689527) uniform_distr
KstestResult(statistic=0.37693207560769215, pvalue=0.0) expon_distr


###### Тест Колмогорова-Смирнова  'expon'  экспоненциальное

In [25]:
for distr, name in distr_name:
    print(stats.kstest(distr, 'expon'), name)

KstestResult(statistic=0.5078212454826238, pvalue=0.0) normal_distr
KstestResult(statistic=0.36796915000790165, pvalue=0.0) uniform_distr
KstestResult(statistic=0.01423008548425575, pvalue=0.26102795645666543) expon_distr


###### тест 2 
Увеличим выборку в 4 раза

In [26]:
size = 4999 * 4
normal_distr = stats.norm.rvs(size=size)
uniform_distr = stats.uniform.rvs(size=size)
expon_distr = stats.expon.rvs(size=size)

In [27]:
fig = go.Figure()
fig.add_trace(go.Histogram(x=normal_distr, name='normal_distr',))
fig.add_trace(go.Histogram(x=uniform_distr, name='uniform_distr'))
fig.add_trace(go.Histogram(x=expon_distr, name='expon_distr'))

# Overlay both histograms
fig.update_layout(barmode='overlay')
# Reduce opacity to see both histograms
fig.update_traces(opacity=0.5)
fig.show()

In [28]:
distr_name = list(
    zip(
        (normal_distr, uniform_distr, expon_distr),
        ('normal_distr', 'uniform_distr', 'expon_distr')
    )
)

###### Tecт Шапиро-Уилки

In [29]:
for distr, name in distr_name:
    print(stats.shapiro(distr), name)

ShapiroResult(statistic=0.9999152421951294, pvalue=0.7747884392738342) normal_distr
ShapiroResult(statistic=0.9549716711044312, pvalue=0.0) uniform_distr
ShapiroResult(statistic=0.8111166954040527, pvalue=0.0) expon_distr


C:\ProgramData\Anaconda3\lib\site-packages\scipy\stats\_morestats.py:1800: UserWarning:

p-value may not be accurate for N > 5000.



###### Тест Колмогорова-Смирнова  'norm' нормальное

In [30]:
for distr, name in distr_name:
    print(stats.kstest(distr, 'norm'), name)

KstestResult(statistic=0.004093791395320956, pvalue=0.8895275615768691) normal_distr
KstestResult(statistic=0.5000808105147736, pvalue=0.0) uniform_distr
KstestResult(statistic=0.5000424092230357, pvalue=0.0) expon_distr


###### Тест Колмогорова-Смирнова  'uniform' равномерное

In [31]:
for distr, name in distr_name:
    print(stats.kstest(distr, 'uniform'), name)

KstestResult(statistic=0.5001803527837931, pvalue=0.0) normal_distr
KstestResult(statistic=0.0052195441947484045, pvalue=0.6452741430885605) uniform_distr
KstestResult(statistic=0.3744748949789958, pvalue=0.0) expon_distr


###### Тест Колмогорова-Смирнова  'expon'  экспоненциальное

In [32]:
for distr, name in distr_name:
    print(stats.kstest(distr, 'expon'), name)

KstestResult(statistic=0.5001803769220535, pvalue=0.0) normal_distr
KstestResult(statistic=0.36790048225874694, pvalue=0.0) uniform_distr
KstestResult(statistic=0.006902251286856176, pvalue=0.2952396357901952) expon_distr


### distfit

Для Windows
- WIN + R
- Ввести cmd и нажать ENTER
- Ввести команду и нажать ENTER:

In [33]:
#pip install distfit (Установить пакет)
from distfit import distfit

In [34]:
# Initialize for discrete distribution fitting
dfit = distfit(distr=[
    'norm', 'uniform', 'expon'
])

# Run distfit to and determine whether we can find the parameters from the data.
result = dfit.fit_transform(uniform_distr)

[distfit] >INFO> fit
[distfit] >INFO> transform
[distfit] >INFO> [norm   ] [0.00 sec] [RSS: 3.64026] [loc=0.499 scale=0.288]
[distfit] >INFO> [uniform] [0.00 sec] [RSS: 0.0270325] [loc=0.000 scale=1.000]
[distfit] >INFO> [expon  ] [0.00 sec] [RSS: 7.02922] [loc=0.000 scale=0.499]
[distfit] >INFO> Compute confidence intervals [parametric]


In [35]:
result['model']

{'name': 'uniform',
 'score': 0.027032528206786425,
 'loc': 0.00020256192260414974,
 'scale': 0.999740244107731,
 'arg': (),
 'params': (0.00020256192260414974, 0.999740244107731),
 'model': <scipy.stats._distn_infrastructure.rv_continuous_frozen at 0x1a3cdec54c0>,
 'bootstrap_score': 0,
 'bootstrap_pass': None,
 'color': '#e41a1c',
 'CII_min_alpha': 0.0501895741279907,
 'CII_max_alpha': 0.9499557938249485}